In [1]:
import os
import json

from tqdm import tqdm
import pandas as pd # 여기에 있으면 안됨. 함수화 필요

from configs import build_exp, EnvDefineUnit
from data_engineering.dataset.precendent import CSVPrecendentDataset, install_pipeline # 이전사례 데이터 추상화 실패
from data_engineering.prompt_engineering.LLM_template import get_prompt_template
from data_engineering.prompt_engineering.precendent_to_docs import get_prompt_precendent
from data_engineering.prompt_engineering.precendent_to_question import get_prompt_question
from data_engineering.dataset.guideline import PDFDataset
from data_engineering.RAG import get_splitter, VectorstoreDefineTool
from core import load_LLM, ChainControlTool
from utils.now import get_now


/home/container_user/.cache/pypoetry/virtualenvs/hansoldeco3-QckXwucX-py3.11/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
exp = 'exp_3'

env = EnvDefineUnit()
config_exp = build_exp(exp)
now = get_now("Asia/Seoul")


# 경로 - path manager 추상화 실패
path_train = os.path.join(env.PATH_DATA_DIR, config_exp.train)
path_test = os.path.join(env.PATH_DATA_DIR, config_exp.test)
paths_pdf = os.path.join(env.PATH_DATA_DIR, 'raw', '건설안전지침')
paths_pdf = [os.path.join(paths_pdf, x) for x in os.listdir(paths_pdf)]
path_exp = os.path.join(env.PATH_LOG_DIR, "exp", now)


# 실험 파라미터, 현재 함수는 추후 쪼개질 수 있으므로 변수 하나하나 따로 선언
encoding = config_exp.data_encoding
pipeline = config_exp.data_pipeline
version_prompt_precendent = config_exp.version_prompt_precendent
version_prompt_question = config_exp.version_prompt_question

retriever_precendent_name = config_exp.retriever_precendent_name
retriever_guideline_name = config_exp.retriever_guideline_name
embedding_model_name_precendent = config_exp.embedding_model_name_precendent
embedding_model_name_guideline = config_exp.embedding_model_name_guideline
prompt_template_format = config_exp.prompt_template_format
retriever_precendent_params = config_exp.retriever_precendent_params
retriever_guideline_params = config_exp.retriever_guideline_params
splitter_precendent_name = config_exp.splitter_precendent_name
splitter_precendent_kwargs = config_exp.splitter_precendent_kwargs
splitter_guideline_name = config_exp.splitter_guideline_name
splitter_guideline_kwargs = config_exp.splitter_guideline_kwargs

model_strategy = config_exp.model_strategy
model_name = config_exp.model_name
temperature = config_exp.temperature
top_p = config_exp.top_p
top_k = config_exp.top_k
max_new_tokens = config_exp.max_new_tokens

chain_strategy = config_exp.chain_strategy
chain_type = config_exp.chain_type

In [3]:
# 테스트 데이터 로드
pipeline = install_pipeline(pipeline)
test_data = pd.read_csv(path_test, encoding = encoding)
test_data = pipeline(test_data)


precendent = pd.read_csv(path_train, encoding = encoding)
precendent = pipeline(precendent) # 이전사례 데이터와 질문용 테스트 데이터는 전처리가 달라질 수 있음

/workspace/Projects/hansoldeco3/src/data_engineering/dataset/precendent/preprocess/cleaning.py:119: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '겨울' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df_.loc[winter,col2] = '겨울'
/workspace/Projects/hansoldeco3/src/data_engineering/dataset/precendent/preprocess/cleaning.py:135: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '아침' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  df_.loc[morning,col2] = '아침'
/workspace/Projects/hansoldeco3/src/data_engineering/dataset/precendent/preprocess/cleaning.py:119: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '겨울' has dtype incompatible with float64, please explicitly cast to

In [4]:
precendent.columns

Index(['발생일시', '시간대', '계절', '사고인지 시간', '사고인지시차', '근무종류', '날씨', '기온', '습도',
       '공사종류_대분류', '공사종류_중분류', '공사종류_소분류', '연면적', '지상', '지하', '인적사고', '물적사고',
       '공종_대분류', '공종_소분류', '사고객체_대분류', '사고객체_소분류', '작업프로세스', '장소', '부위2',
       '사고원인', '재발방지대책 및 향후조치계획'],
      dtype='object')

In [26]:
precendent.columns

Index(['발생일시', '사고인지 시간', '근무종류', '날씨', '기온', '습도', '공사종류_대분류', '공사종류_중분류',
       '공사종류_소분류', '연면적', '지상', '지하', '인적사고', '물적사고', '공종_대분류', '공종_소분류',
       '사고객체_대분류', '사고객체_소분류', '작업프로세스', '장소', '부위1', '부위2', '사고원인',
       '재발방지대책 및 향후조치계획'],
      dtype='object')

In [13]:
precendent.head()

발생일시 사고인지 시간  근무종류  날씨    기온    습도 공사종류_대분류  \
ID                                                                       
TRAIN_00000 2023-12-31 12:44:00     NaT  정규작업  맑음   1.0  30.0       건축   
TRAIN_00001 2023-12-30 15:35:00     NaT  정규작업  맑음  10.0  90.0       토목   
TRAIN_00002 2023-12-30 14:30:00     NaT  정규작업  맑음  14.0  70.0       건축   
TRAIN_00003 2023-12-30 12:00:00     NaT  휴일근무  흐림  12.0  55.0       토목   
TRAIN_00004 2023-12-30 10:00:00     NaT  정규작업  맑음   0.0  10.0       건축   

            공사종류_중분류 공사종류_소분류       연면적  ...  공종_대분류     공종_소분류 사고객체_대분류  \
ID                                       ...                               
TRAIN_00000      건축물   근린생활시설   4892.77  ...      건축   철근콘크리트공사     건설자재   
TRAIN_00001       터널     철도터널       NaN  ...      토목       터널공사     건설자재   
TRAIN_00002      건축물     업무시설   1994.62  ...      건축   철근콘크리트공사       기타   
TRAIN_00003       하천       기타       NaN  ...      토목       하천공사       부재   
TRAIN_00004      건축물     공동주택  59388.93  ...      건축  해체 및 철거공사       기타   

            사고객체_소분류   작업프로세스             장소    부위1 부위2  \
ID                                                        
TRAIN_00000       철근     설치작업    근린생활시설 / 내부     철근  고소   
TRAIN_00001       볼트     운반작업      철도터널 / 내부     볼트  바닥   
TRAIN_00002       기타  형틀 및 목공      업무시설 / 내부     기타  바닥   
TRAIN_00003    교각 기초     조립작업  기타 / 동산교 신축구간  교각 기초  바닥   
TRAIN_00004    건설폐기물     해체작업      공동주택 / 내부  건설폐기물  바닥   

                                                          사고원인  \
ID                                                               
TRAIN_00000  고소작업 중 추락 위험이 있음에도 불구하고, 안전난간대, 안전고리 착용 등 안전장치...   
TRAIN_00001                                                부주의   
TRAIN_00002                               3층 슬라브 작업시 이동중  미끄러짐   
TRAIN_00003  교각 기초철근 조립 중 강한 바람에 의해 기둥측 주철근이 균형을 잃고 전도되어, 하...   
TRAIN_00004                                           근로자의 부주의   

                                               재발방지대책 및 향후조치계획  
ID                                                              
TRAIN_00000                      고소작업 시 추락 위험이 있는 부위에 안전장비 설치.  
TRAIN_00001                              재발 방지 대책 마련과 안전교육 실시.  
TRAIN_00002  현장자재 정리와 안전관리 철저를 통한 재발 방지 대책 및 공문 발송을 통한 향후 조...  
TRAIN_00003  위험성 평가 및 교육을 통해 작업장 내 위험요인과 안전수칙을 근로자에게 전파하고, ...  
TRAIN_00004  자재 정리 작업 시 세부 작업 방법에 대한 교육 실시와 작업 구간 이동 경로 점검 ...  

[5 rows x 24 columns]

In [19]:
precendent['사고인지 시간']

ID
TRAIN_00000                   NaT
TRAIN_00001                   NaT
TRAIN_00002                   NaT
TRAIN_00003                   NaT
TRAIN_00004                   NaT
                      ...        
TRAIN_23417                   NaT
TRAIN_23418   2019-07-03 15:00:00
TRAIN_23419                   NaT
TRAIN_23420                   NaT
TRAIN_23421                   NaT
Name: 사고인지 시간, Length: 23322, dtype: datetime64[ns]

In [18]:
precendent.columns

Index(['발생일시', '사고인지 시간', '근무종류', '날씨', '기온', '습도', '공사종류_대분류', '공사종류_중분류',
       '공사종류_소분류', '연면적', '지상', '지하', '인적사고', '물적사고', '공종_대분류', '공종_소분류',
       '사고객체_대분류', '사고객체_소분류', '작업프로세스', '장소', '부위1', '부위2', '사고원인',
       '재발방지대책 및 향후조치계획'],
      dtype='object')

In [2]:
import numpy as np

In [3]:
a = pd.read_csv("/workspace/Storage/hansoldeco3/Log/TA.csv")

In [4]:
a['answer'] = a['answer'].apply(lambda x: x if any(c.isdigit() for c in x) else np.nan)


In [5]:
for i, row in a.iterrows():
    if pd.isna(row['answer']):
        continue
    if '1)' in a['answer'][i]:
        a['answer'][i] = np.nan

/tmp/ipykernel_240402/3411681589.py:5: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  a['answer'][i] = np.nan
/tmp/ipykernel_240402/3411681589.py:5: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting v

In [6]:
a['answer'].isna().sum()

10746

In [7]:
a

ID                                    재발방지대책 및 향후조치계획  \
0      TRAIN_00000                      고소작업 시 추락 위험이 있는 부위에 안전장비 설치.   
1      TRAIN_00001                              재발 방지 대책 마련과 안전교육 실시.   
2      TRAIN_00002  현장자재 정리와 안전관리 철저를 통한 재발 방지 대책 및 공문 발송을 통한 향후 조...   
3      TRAIN_00003  위험성 평가 및 교육을 통해 작업장 내 위험요인과 안전수칙을 근로자에게 전파하고, ...   
4      TRAIN_00004  자재 정리 작업 시 세부 작업 방법에 대한 교육 실시와 작업 구간 이동 경로 점검 ...   
...            ...                                                ...   
23417  TRAIN_23417                             현장안전관리와 일용근로자 교육의 철저함.   
23418  TRAIN_23418  근로자 안전교육 실시 및 관리감독 강화를 통한 사고 방지 대책과 안전교육 강화를 포...   
23419  TRAIN_23419  작업자 안전수칙 교육 철저와 재해 사례 전파 및 안전교육 실시, 안전수칙 준수 철저...   
23420  TRAIN_23420   해당작업에 맞는 개인보호구 지급 및 점검관리, 공사참여자 안전관리교육, 시공관리 실시.   
23421  TRAIN_23421  작업전 교육과 작업시 안전관리를 철저히 시행하여 준공완료를 목표로 하는 재발 방지 대책.   

              answer  
0         \n1\n\nA:   
1                NaN  
2             3\nA:   
3                NaN  
4                NaN  
...              ...  
23417            NaN  
23418            NaN  
23419   \n\nA: 4\n\n  
23420       3\n\nA:   
23421            NaN  

[23422 rows x 3 columns]

In [35]:
import numpy as np

In [8]:
a.to_csv('/workspace/Storage/hansoldeco3/Log/TA.csv',index=False)